In [ ]:
import random
import numpy as np
import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d import Axes3D

# ---- Direction and inverse maps ----
DIR_VECT = {
    'n': (0, 1, 0), 's': (0, -1, 0),
    'e': (1, 0, 0), 'w': (-1, 0, 0),
    'u': (0, 0, 1), 'd': (0, 0, -1),
}
INV = {'n':'s','s':'n','e':'w','w':'e','u':'d','d':'u'}
POS_AXES = {'x':('e','w'), 'y':('n','s'), 'z':('u','d')}

# ---- Helpers ----
def reduce_word(word):
    stack = []
    for ch in word:
        if stack and INV[ch] == stack[-1]:
            stack.pop()
        else:
            stack.append(ch)
    return stack

def word_to_vertices(word):
    x = y = z = 0
    verts = [(x,y,z)]
    for ch in word:
        dx,dy,dz = DIR_VECT[ch]
        x += dx; y += dy; z += dz
        verts.append((x,y,z))
    return verts

def is_closed(word):
    verts = word_to_vertices(word)
    return verts[0] == verts[-1]

def is_self_avoiding(word):
    verts = word_to_vertices(word)
    return len(set(verts[:-1])) == len(verts[:-1])

def is_valid_knot(word):
    w = reduce_word(list(word))
    return is_closed(w) and is_self_avoiding(w) and len(w) >= 4

# ---- Operations ----
def apply_elementary_switch(word):
    w = list(word)
    if not w: return w
    start = random.randrange(0, len(w))
    end = random.randint(start+1, min(len(w), start+6))
    wrap_dir = random.choice(['e','n','u' , 'w' , 's' , 'd'])
    inv = INV[wrap_dir]
    new = w[:start] + [wrap_dir] + w[start:end] + [inv] + w[end:]
    s =  reduce_word(new)
    if(is_valid_knot(s)):
        return s
    else:
        return ""
def apply_doubling(word):
    axis = random.choice(['x','y','z'])
    a_pos, a_neg = POS_AXES[axis]
    new = []
    for ch in word:
        if ch in (a_pos,a_neg): new += [ch,ch]
        else: new.append(ch)
    return reduce_word(new)

def apply_halving(word):
    if not word:
        return []

    axis = random.choice(['x', 'y', 'z'])
    a_pos, a_neg = POS_AXES[axis]

    w = list(word)
    n = len(w)
    runs = []
    i = 0
    valid_to_halve = True
    while i < n:
        ch = w[i]
        if ch in (a_pos, a_neg):
            j = i
            while j < n and w[j] == ch:
                j += 1
            run_len = j - i
            runs.append((i, j, ch, run_len))
            if run_len < 2:
                valid_to_halve = False
            i = j
        else:
            i += 1

    if not runs or not valid_to_halve:
        return w

    new = []
    i = 0
    for start, end, ch, run_len in runs:
        while len(new) < start and i < start:
            new.append(w[i])
            i += 1
        new.extend([ch] * (run_len - 1))
        i = end

    while i < n:
        new.append(w[i])
        i += 1

    reduced = reduce_word(new)
    return reduced





Below is a randomized version . Where we apply the elementary switches randomly and visualize how the knot changes

In [ ]:
# ---- Random evolution ----
def run_random_sequence(initial, steps=50, seed=None):
    if seed: random.seed(seed)
    cur = reduce_word(list(initial))
    if not is_valid_knot(cur):
        print("Not a knot")
        return []
    print("Valid knot")
    seq = [cur]
    for _ in range(steps):
        op = 'switch'
        if op == 'switch': cand = apply_elementary_switch(cur)
        elif op == 'double': cand = apply_doubling(cur)
        else: cand = apply_halving(cur)
        if is_valid_knot(cand):
            cur = cand
            seq.append(cur)
    return seq

import plotly.graph_objects as go
import numpy as np

def animate_word_sequence_plotly(word_sequence, interval=600):
    # Convert each word to vertices array
    frames_data = [np.array(word_to_vertices(w)) for w in word_sequence]

    # Compute bounds for all points
    all_pts = np.vstack(frames_data)
    mins, maxs = all_pts.min(axis=0), all_pts.max(axis=0)
    rng = (maxs - mins).max()
    mid = (maxs + mins) / 2.0

    # --- Create figure ---
    fig = go.Figure(
        data=[
            go.Scatter3d(
                x=frames_data[0][:,0],
                y=frames_data[0][:,1],
                z=frames_data[0][:,2],
                mode="lines+markers",
                line=dict(width=6, color="royalblue"),
                marker=dict(size=4, color="orange")
            )
        ],
        layout=go.Layout(
            scene=dict(
                xaxis=dict(range=[mid[0]-rng/2, mid[0]+rng/2], title='X'),
                yaxis=dict(range=[mid[1]-rng/2, mid[1]+rng/2], title='Y'),
                zaxis=dict(range=[mid[2]-rng/2, mid[2]+rng/2], title='Z'),
                aspectmode='cube'
            ),
            margin=dict(l=0, r=0, b=0, t=30),
            title="Lattice Knot Evolution",
            updatemenus=[{
                "type": "buttons",
                "showactive": False,
                "buttons": [
                    {
                        "label": "▶ Play",
                        "method": "animate",
                        "args": [None, {"frame": {"duration": interval, "redraw": True}, "fromcurrent": True}]
                    },
                    {
                        "label": "⏸ Pause",
                        "method": "animate",
                        "args": [[None], {"frame": {"duration": 0, "redraw": False}, "mode": "immediate"}]
                    }
                ]
            }]
        )
    )

    # --- Add frames ---
    frames = []
    for i, pts in enumerate(frames_data):
        frame = go.Frame(
            data=[
                go.Scatter3d(
                    x=pts[:,0],
                    y=pts[:,1],
                    z=pts[:,2],
                    mode="lines+markers",
                    line=dict(width=6, color="royalblue"),
                    marker=dict(size=4, color="orange")
                )
            ],
            name=f"frame{i}"
        )
        frames.append(frame)
    fig.frames = frames

    fig.show()
initial = "nnneseswsw"   # or any valid knot word
seq= run_random_sequence(initial, steps=500, seed=42)
print(seq)
animate_word_sequence_plotly(seq, interval=50)

Valid knot
[['n', 'n', 'n', 'e', 's', 'e', 's', 'w', 's', 'w'], ['n', 'd', 'n', 'u', 'n', 'e', 's', 'e', 's', 'w', 's', 'w'], ['n', 'd', 'n', 'u', 'n', 'n', 'e', 's', 's', 'e', 's', 'w', 's', 'w'], ['n', 'd', 'n', 'u', 'n', 'n', 'e', 's', 's', 'e', 's', 'w', 's', 'w'], ['n', 'd', 'n', 'u', 'n', 'n', 'e', 's', 's', 'e', 's', 'w', 's', 'w'], ['n', 'n', 'n', 'n', 'e', 's', 's', 'e', 's', 'w', 's', 'w'], ['n', 'n', 'n', 'n', 'e', 's', 's', 'e', 's', 'w', 's', 'w'], ['n', 'n', 'n', 'd', 'n', 'e', 's', 's', 'e', 's', 'u', 'w', 's', 'w'], ['n', 'n', 'd', 'n', 'e', 's', 'e', 's', 'u', 'w', 's', 'w'], ['n', 'n', 'd', 'n', 'n', 'e', 's', 's', 'e', 's', 'u', 'w', 's', 'w'], ['n', 'n', 'd', 'n', 'n', 'e', 's', 's', 'e', 's', 'u', 'u', 'w', 's', 'd', 'w'], ['n', 'n', 'd', 'n', 'n', 'e', 's', 'e', 's', 's', 'u', 'u', 'w', 's', 'd', 'w'], ['n', 'n', 'd', 'n', 'n', 'e', 's', 'e', 's', 's', 'e', 'u', 'w', 'u', 'w', 's', 'd', 'w'], ['n', 'n', 'd', 'n', 'n', 'e', 's', 'e', 's', 's', 'e', 'u', 'u', 'w', '

Here is bruteforce version which applies all possible elementary switches but caps if it becomes too many

In [27]:
def generate_elementary_switches(word):
    w = list(word)
    if not w:
        return []

    directions = list(INV.keys())  # e.g. ['e','n','u','w','s','d']
    results = set()

    L = len(w)
    # start in 0..L-1, end in start+1..L  (inserting around at least one element)
    for start in range(0, L):
        for end in range(start + 1, L + 1):
            for dir_ in directions:
                inv = INV[dir_]
                new = w[:start] + [dir_] + w[start:end] + [inv] + w[end:]
                # reduce_word should accept a list and return a string/list consistent
                s = reduce_word(new)
                if s and is_valid_knot(s):
                    # Normalize representation (e.g. string) so duplicates can be removed
                    # If reduce_word returns list, convert to string: join
                    if isinstance(s, list):
                        s_str = ''.join(s)
                    else:
                        s_str = s
                    results.add(s_str)

    return list(results)


# --- New runner: build levels of all possibilities per stage ---
def run_exhaustive_levels(initial, depth=6, seed=None, max_nodes_per_level=200, target=None):
    """
    Build a list of levels (each level is a list of words).
    - initial: initial word string (or list acceptable by reduce_word)
    - depth: number of steps (levels) to expand
    - max_nodes_per_level: optional cap per level to avoid explosion (None for no cap)
    - target: optional string to check for appearance in any generated level
    Returns: (levels, found_info) where found_info is None or (level_idx, index_in_level, word)
    """
    if seed is not None:
        random.seed(seed)

    cur = reduce_word(list(initial))
    if not is_valid_knot(cur):
        print("Not a knot")
        return [], None

    # Normalize initial to string
    if isinstance(cur, list):
        cur = ''.join(cur)

    # Normalize target if provided
    found_info = None
    if target is not None:
        t_reduced = reduce_word(list(target))
        if isinstance(t_reduced, list):
            t_reduced = ''.join(t_reduced)
        # quick check: if target reduces same as initial, immediate equivalence
        if t_reduced == cur:
            print(f"Equivalent — target reduces to same as initial (both: {cur}).")
            return [[cur]], (0, 0, cur)
    else:
        t_reduced = None

    print("Valid knot:", cur)
    levels = [[cur]]

    for d in range(depth):
        next_level_set = set()
        for word in levels[-1]:
            children = generate_elementary_switches(word)
            for c in children:
                next_level_set.add(c)

        # Optionally limit level size deterministically (sort then take first N)
        next_level = sorted(next_level_set)
        if max_nodes_per_level is not None and len(next_level) > max_nodes_per_level:
            next_level = next_level[:max_nodes_per_level]

        # If nothing new was generated, stop early
        if not next_level:
            break

        # Before appending, check if target appears in next_level
        if t_reduced is not None and not found_info:
            for idx, w in enumerate(next_level):
                if w == t_reduced:
                    found_info = (d+1, idx, w)  # level index is d+1 (since levels[0] is initial)
                    print(f"Equivalent — found target at level {d+1} index {idx}: {w}")
                    break

        levels.append(next_level)

    # Final full-scan (in case target was in initial or earlier levels)
    if t_reduced is not None and not found_info:
        for lvl_idx, level in enumerate(levels):
            for idx, w in enumerate(level):
                if w == t_reduced:
                    found_info = (lvl_idx, idx, w)
                    print(f"Equivalent — found target at level {lvl_idx} index {idx}: {w}")
                    break
            if found_info:
                break

    if t_reduced is not None and not found_info:
        print(f"No evidence of equivalence found after depth {len(levels)-1} (levels generated).")

    return levels, found_info


# --- Animator: show multiple candidates per frame (one frame per level) ---
def animate_word_levels_plotly(word_levels, interval=600):
    """
    Animate candidates one-by-one:
      - word_levels: list of lists of words (level -> list of words)
      - Each frame shows exactly one candidate and an annotation "Level L — candidate i/N"
    """
    # Build list of (level, index, word) tuples preserving order level by level
    ordered = []
    for lvl_idx, level in enumerate(word_levels):
        for i, w in enumerate(level):
            ordered.append((lvl_idx, i, w))

    if not ordered:
        print("No candidates to animate.")
        return

    # Precompute pts for each candidate; skip candidates that fail to convert
    frames_data = []
    for (lvl, i, w) in ordered:
        try:
            pts = np.array(word_to_vertices(w))
            if pts.size == 0:
                print(f"Skipping empty vertices: level {lvl} idx {i}")
                continue
            frames_data.append((lvl, i, w, pts))
        except Exception as e:
            print(f"Skipping candidate level {lvl} idx {i} due to error: {e}")
            continue

    if not frames_data:
        print("No valid vertex data to animate after conversion.")
        return

    # compute global bounds across all candidate points
    all_pts = np.vstack([pts for (_, _, _, pts) in frames_data])
    mins, maxs = all_pts.min(axis=0), all_pts.max(axis=0)
    rng = (maxs - mins).max() if all_pts.size else 1.0
    mid = (maxs + mins) / 2.0

    # Create initial trace using the first candidate
    first_lvl, first_i, first_w, first_pts = frames_data[0]
    init_trace = go.Scatter3d(
        x=first_pts[:,0],
        y=first_pts[:,1],
        z=first_pts[:,2],
        mode="lines+markers",
        line=dict(width=6),
        marker=dict(size=4),
        name=f"level{first_lvl}_idx{first_i}"
    )

    # initial annotation text
    total_in_level = len(word_levels[first_lvl]) if first_lvl < len(word_levels) else 1
    ann_text = f"Level {first_lvl} — candidate {first_i+1} / {total_in_level}"

    fig = go.Figure(
        data=[init_trace],
        layout=go.Layout(
            scene=dict(
                xaxis=dict(range=[mid[0]-rng/2, mid[0]+rng/2], title='X'),
                yaxis=dict(range=[mid[1]-rng/2, mid[1]+rng/2], title='Y'),
                zaxis=dict(range=[mid[2]-rng/2, mid[2]+rng/2], title='Z'),
                aspectmode='cube'
            ),
            margin=dict(l=0, r=0, b=0, t=40),
            title="Lattice Knot Evolution — single candidate stepping",
            annotations=[dict(
                text=ann_text,
                x=0.5, y=0.95, xref='paper', yref='paper',
                showarrow=False, font=dict(size=14)
            )],
            updatemenus=[{
                "type": "buttons",
                "showactive": False,
                "buttons": [
                    {
                        "label": "▶ Play",
                        "method": "animate",
                        "args": [None, {"frame": {"duration": interval, "redraw": True}, "fromcurrent": True}]
                    },
                    {
                        "label": "⏸ Pause",
                        "method": "animate",
                        "args": [[None], {"frame": {"duration": 0, "redraw": False}, "mode": "immediate"}]
                    }
                ]
            }]
        )
    )

    # Build one frame per candidate (single trace + layout.annotation for label)
    frames = []
    for (lvl, i, w, pts) in frames_data:
        # name and annotation
        total_in_level = len(word_levels[lvl]) if lvl < len(word_levels) else 1
        label = f"Level {lvl} — candidate {i+1} / {total_in_level}"
        # single trace for this candidate
        tr = go.Scatter3d(
            x=pts[:,0],
            y=pts[:,1],
            z=pts[:,2],
            mode="lines+markers",
            line=dict(width=6),
            marker=dict(size=4),
            name=f"level{lvl}_idx{i}"
        )
        # attach a layout with annotation so label updates per frame
        frame_layout = go.Layout(annotations=[dict(
            text=label, x=0.5, y=0.95, xref='paper', yref='paper',
            showarrow=False, font=dict(size=14)
        )])
        frame = go.Frame(data=[tr], name=f"lvl{lvl}_i{i}", layout=frame_layout)
        frames.append(frame)
        #print(f"Prepared frame: {label}")   # console feedback while building

    fig.frames = frames
    fig.show()




# --- Example usage ---
initial = "nnneseswsw"   # or any valid knot word
target = "nnessw"    # target string to check for equivalence

# Build exhaustive tree of possibilities (levels) and check target
levels, found = run_exhaustive_levels(initial, depth=3, seed=42, max_nodes_per_level=500, target=target)
for i, lvl in enumerate(levels):
    print(f"Step {i}: {len(lvl)} candidates")

# Visualize
animate_word_levels_plotly(levels, interval=20)


Valid knot: nnneseswsw
Equivalent — found target at level 1 index 33: nnessw
Step 0: 1 candidates
Step 1: 143 candidates
Step 2: 500 candidates
Step 3: 500 candidates
